## konlpy로 synop 명사 추출
## TfidfVectorizer, cosine_similarity

문서간의 거리(유사도)  동일 계산임
1. documnet_distance = (tfidf_matrix * tfidf_matrix.T)
2. cosine_sim = cosine_similarity(tfidf_matrix, tfidf_matrix)

In [61]:
import pandas as pd
import numpy as np
import unicodedata
from konlpy.tag import *
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity

In [62]:
metadata = pd.read_csv('id_sorted.csv', encoding='cp949')


In [63]:
metadata.head(1)

id   tv     title                               epi       dates  \
0   1  SBS  그것이 알고싶다  되살아난 연쇄살인의 공포 - 부녀자 연쇄 피습 사건의 진실  2004-07-03   

                                               links  \
0  http://programs.sbs.co.kr/culture/unansweredqu...   

                                               synop    vod_key  \
0   제 목  되살아난 연쇄살인의 공포  부녀자 연쇄 피습 사건의 진실  방송일시  2...  범죄', '흉기'   

                                               image class  awards  
0  //img2.sbs.co.kr/img/sbs_cms/SR/2015/12/08/SR4...    기타       0

In [64]:
metadata['synop'][755]

'어느 강력반 형사의 죽음방송일시   2010년 12월 4일 토  밤 11시 00분익사체로 발견된 서울 강남경찰서 강력반 형사지난 7월 29일 낮. 충북 영동의 한 낚시터에서 심하게 부패된 시신 한 구가 떠올랐다. 사체를 인양한 119 소방대원과 경찰들을 놀라게 한 것은 바지 뒷주머니에서 발견된 신분증. 그는 서울 강남경찰서 강력반 소속의 이OO 형사였던 것이다. 이틀 전 출근도 안한 채 사라져 실종신고까지 되어 있던 그는 싸늘한 시신이 되어 발견되었고  사인규명에 나선 경찰은 수사 한 달여 만인 지난 8월 27일 이 형사 스스로 물에 빠져 익사한 것으로 추정된다며 자살로 내사 종결했다자살인가 타살인가    끝나지 않은 의문들이 형사는 실종 당일 아침 출근하겠다고 상사와 통화한 후 갑자기 자신의 차로 부산으로 향하기 시작했다. 고속도로 주행 중 교통사고를 내고 영동의 한 병원으로 옮겨진 이 형사는 화장실을 간다며 사라져 버렸다. 그리고 그 후 시신으로 발견되기까지 이 형사의 행적은 드러나고 있지 않다. 병원에서 멀리 떨어진 외딴 저수지  자살이라면 이 형사는 그 곳까지 어떻게 갔으며 왜 스스로 물에 빠져 죽음을 선택한 것일까  또한 이 형사는 무슨 일로 부산으로 급하게 내려가려고 했고  왜 병원에서 사라졌는가 시신이 말하는 진실   과연 그는 어떻게 죽었는가 유족들은 이형사가 자살할 이유가 전혀 없다며 재수사를 요구하고 있다. 특히  저수지의 사체 발견 장소 깊이가 허리 높이 정도 밖에 안 되는데도 자살로 인한 익사로 처리한 것엔 문제가 많다는 주장이다. 과연 이 형사는 그 저수지에서 스스로 물에 빠져 자살한 것일까  국립과학수사연구소는 부패로 사인을 정확히 알 수는 없으나 폐에서 플랑크톤이 발견된 점 등으로 보아 익사의 가능성을 배제할 수 없다는 의견을 내놓은 상태.  그것이 알고싶다 는 이 형사의 사인을 정확히 알아내기 위해 국내의 법의학자들과 일본의 법의학자에게 분석을 의뢰했다. 그 결과는 의외였다. 부검 결과만으로는 익사의 증거가 될 수 없으며  오히려

In [65]:
len(metadata['synop'])

2747

In [66]:
han = Hannanum()

In [67]:
synoplist = metadata['synop']
synoplist.head()

0     제 목  되살아난 연쇄살인의 공포  부녀자 연쇄 피습 사건의 진실  방송일시  2...
1      2004 행복신드롬   당신은 웰빙하고 계십니까   웰빙은 즐거운 변화   늘어...
2    지금 우리는 국민소득 2만 달러 달성과 선진국 진입의 중요한 기로에 서 있다. 자원...
3     21명 연쇄살인 피의자  유영철의 진실은 무엇인가  무고한 시민 21명을 살해한 ...
4     누구도 축복해 주지 않는 출산의 공포 임신이라는 말에 연락을 끊어버린 남자친구  ...
Name: synop, dtype: object

In [68]:
# 불용어 제거 안함.
han.nouns(synoplist[0])

['저',
 '목',
 '연쇄살인',
 '공포',
 '부녀',
 '연쇄',
 '피습',
 '사건',
 '진실',
 '방송일시',
 '2004년',
 '7월',
 '03일',
 '밤11시05분',
 '윤',
 '성',
 '작',
 '류',
 '혜',
 '린서울',
 '서남부',
 '지역',
 '반경',
 '4Km',
 '안',
 '2월',
 '5월사이',
 '부녀',
 '피습사건',
 '4건',
 '발생',
 '3명',
 '1명',
 '목숨',
 '지금',
 '경찰',
 '것',
 '금품',
 '성폭행',
 '흔적',
 '사실',
 '범행',
 '동기',
 '불분명',
 '범행수법',
 '잔혹',
 '이유',
 '범죄',
 '조심',
 '추정',
 '인터넷',
 '공포',
 '괴담',
 '지',
 '범인',
 '특정',
 '버스',
 '노선',
 '하얀색',
 '옷',
 '여자',
 '죽',
 '며',
 '근거',
 '소문',
 '확산',
 '서남부지역',
 '주민들',
 '서울판',
 '살인',
 '추억',
 '것',
 '아니냐',
 '불안',
 '동기',
 '범죄',
 '사람',
 '찔렀어요지난',
 '5월',
 '9일',
 '02시',
 '보라매',
 '공원',
 '남문',
 '오솔길',
 '여대생',
 '김모',
 '22',
 '양',
 '졸업',
 '의상',
 '구입',
 '귀가도중',
 '괴한',
 '가슴',
 '옆구리',
 '등',
 '흉기',
 '살해',
 '범행',
 '시간',
 '남자친구',
 '통화한',
 '01시57분10초',
 '59분20초사',
 '2분',
 '10초',
 '김모',
 '22',
 '양',
 '일',
 '것',
 '그녀',
 '마지막',
 '말',
 '사람',
 '피해자',
 '주변',
 '뚜렷',
 '단서',
 '경찰',
 '수사',
 '한달',
 '목요일',
 '새벽',
 '연쇄범죄인',
 '단독범죄인가지난',
 '2월',
 '26일',
 '새벽',
 '신림시장',
 '새벽일하러간',
 '할머니',
 '배웅',
 '여

In [69]:
# 에피소드 제목의 명사를 계산에 사용?
#불용어 제거 안함
epilist = metadata['epi']
han.nouns(epilist[925])

['당신', '죄인']

In [70]:
s_nounslist = []

for synop in synoplist:
    s_nouns = ' '.join(han.nouns(synop))
    print(s_nouns)
    s_nounslist.append(s_nouns)


저 목 연쇄살인 공포 부녀 연쇄 피습 사건 진실 방송일시 2004년 7월 03일 밤11시05분 윤 성 작 류 혜 린서울 서남부 지역 반경 4Km 안 2월 5월사이 부녀 피습사건 4건 발생 3명 1명 목숨 지금 경찰 것 금품 성폭행 흔적 사실 범행 동기 불분명 범행수법 잔혹 이유 범죄 조심 추정 인터넷 공포 괴담 지 범인 특정 버스 노선 하얀색 옷 여자 죽 며 근거 소문 확산 서남부지역 주민들 서울판 살인 추억 것 아니냐 불안 동기 범죄 사람 찔렀어요지난 5월 9일 02시 보라매 공원 남문 오솔길 여대생 김모 22 양 졸업 의상 구입 귀가도중 괴한 가슴 옆구리 등 흉기 살해 범행 시간 남자친구 통화한 01시57분10초 59분20초사 2분 10초 김모 22 양 일 것 그녀 마지막 말 사람 피해자 주변 뚜렷 단서 경찰 수사 한달 목요일 새벽 연쇄범죄인 단독범죄인가지난 2월 26일 새벽 신림시장 새벽일하러간 할머니 배웅 여고생 박모 18 양 괴한 흉기 가슴 등 13차례 리 중상 4월22 고척동 여대생 송모 20 양 자신 현관문 열쇠 채 흉기 7차례 사망 5월13 새벽 2시30분 중국교포 한모 39 친구들 술 화장실 흉기 사망 서남부지역 발생 부녀 피습사건 의혹들 속 연쇄범죄 가능성 제 그것 수사전담반 20 간 동행취재 날 복잡해지 다양 범죄 해결하기위한 방법 해외 사례 범죄심리 전문가들 진단
2004 행복신드롬 당신 웰빙하 웰빙 변화 웰빙족케이블 방송 프로듀서 이 삶 방식에푹 웰빙 관련 프로그램 제작 것들을자신 생활 속 체험 것 그녀 유기농 채식 뷔페 커피 잔 유기농 커피전문점 얼마 전 요가원 최근에는필라티스라 종류 운동 일주일 번 스파 센터 족욕 아로마 테라피를즐기 피로 스트레스 방송 제작 일정 속 생활 전 것 없지만그녀 삶 방식 웰빙 자신을변화시키 진정 필요 것 생각 2004년 한국인 화두 웰빙건강 환경 등 관심 증대 신체적 건강하고정신적 여유 삶 을 뜻 웰빙 전 사회 확산 거리 곳곳 요가원 간판 채식 식당 유기농 매장 등 웰빙 시장 은 불황 불구 한 매출 신장 

제목 2004 병풍 커넥션o 방송 2004년 10월 23일 밤 10 55 11 55o 연출 장 경 수 작 홍 아연예 운동선수 병역비 끝 어디 이번 주 경찰 이제까지 병역비 수사 경과 정리 발표 추석 전후 세상 프로야구 선수들 연예 들 병역비 스타급 운동선수들 연예 들 줄 구속 혐의 시 한 이번 사건 전모 무엇 브로커 연루 연예 운동선수들 관계 이번 병역비 사건 뿌리 사진 미스테리 조작 가능한 알부민 커피 병원 사구체신염 신증후군 판정 병역비 연루자들 이것 가능 일 커피 실험 결과 커피 신장질환 유발 것 멀쩡 사람 질병 사람 둔갑 것 면제자들 소변 알부민 때문 임상의사들 병리의사들 임상 소견 것 때 정상 신장조직 병 수 때문 문제 해결 것 이번 병역비 면제자들 조직사진 검사 의사소견서 이해 수 점 진짜 병 것 조직사진 혈액검사 결과 조직검사 들 것 이 것 이유 추적 병무청 두 얼굴이번 사건 병무청 신장관련 질환 면제판정 보류 50 개 질환 면제규정 강화 병역비 사건 때 마다 조치 이번 반복 것 때문 정작병 병역의무 이행 사람 피해 호소 올해 30살 정씨 병역비 때문 병무청 면제판정 23번 신검 지금 병역기피자 피해 호소 엄격 면제규정 집행 병무청 이번 사건 어이 것 병무청 이번 사건 약물 이용 신종수법 이 연예 운동선수 등 관리 사회관심자원 관리제도 97년 이후 때문 수 입장 취재 도중 우리 이번 사건 신종수법 병무청 사회관심자원 리스트 97년 이후 존재 최종 면제판정 병무청 중앙신체검사소 이번 사건 연루자들 소변검사 사실 수 병무청 이번 사건 병역비 침묵 카르텔 방법 병역비 사건 때 마다 수사 뿌리 그것 병역비리 피해자 은밀 당사자 간 거래 완성 때문 때문 병역비 수사 한계 수 밖 이번 수사 경찰 브로커 명단 이외 추 범죄사실 어려움 것 이유 전문가들 상설 수사기구 그때 그때 단발적 병역비 수사 현실 병역비리 시도 것 역부족 지적 병역비리 근절 것 적발율 것 시작 것
제목 끝 살 그 남편 방송 2004년 10월 30일 밤 10 50 연출 덕 거 작 강 영잔혹하

그것 제327회 방송내용ㅇ 제목 대한민국 그들 천국 금발 눈 외국인강사 실태보공 방송일시 2005년 2월 19일 밤 10시55분ㅇ 장 경 수 작 조 한국 여자아이 유혹 법 그것 실화 작년 외국 영어강사들 구인구직 사이트 이태원 한 바 백 들 한국여성들 사진 선정적 이 일부 네티즌들 비난 개인 사생활 의견 논란 대상 사이트 게시판 한국 여자아이 유혹 법 이 제목 글 이 미성년자 성희롱하 내용 사람들 충격 후 비난여론 해당 사이트 자진폐쇄 일 일단락 글 사람 진위여부 소문 일 일부 영어학원 일 무법지대 대마초 학생 외국 강사 지방 한 영어 보습학원 그곳 20대 후반 한 외국 강사 여고생 학원 학생들 대마초 제보 곳 영어 보습학원 중학생 성폭행한 외국 강사 이야기 학원 학원 아이들 외국 강사 충격적 일 수 학원가 강사들 사이 소문 미성년자 부적절 관계 마약관련 이야기 실체 추적 한국 현금인출기 외국 강사 그 한국 생각 돈 수 여성 수 한국 천국 말 외국 강사들 제작진 관광비자 일 대학 학위 위조 개인교습 등 각종 불법적 방법 한국 돈 그 한국 돈 태국 등 동남아 여행 그 한국 현금인출기 나라 말 부적격 영어 강사들 것 백 원어민 강사만 학부모들 영리 학원 브로커 백 불법체류자 단속 뒷짐지고 당국 범죄경력 학위위조 여부 확인 외국인 우리 아이들 현실 불법 거리낌 외국 강사들 이것 영어만능주의 백인선호사상 우리 사회 단면 우리안 인종차별주의 생각한다영어교육 과열 왜곡 집착 동남아 외국근로자 백안시 눈 서양인 관대 우리안 인종차별주의 이상 방치 수 각종 사회적 부작용 이번주 그것 외국 강사들 불법적 고용실태 그것 사회 부정적 영향 대안 취재 영어교육 선행조건 무엇 우리 안 인종차별주의 극복 성숙 사회 수 방안 생각
60년 만 발견 목소리 일제시대 만주국 수도 중국 길림성 장춘 의 동안관 곳 발견 판 45년 3월 가미가제 특공대 출격 직전 녹음 일본군 육성 죽음 목전 사람 답지 특공대 자랑 감회 부모님 동생들 애틋 작별 인사 목소리 담담 애절 확인결과 오오가 마사아키 라 

정진영 그것이알고싶다 337회 방송내용 제목 도벽 죄인 병 방송 2005년 4월 30일 밤 10 50 연출 덕 거 작 강 영 버릇절도죄 청송교도소 복역 출감 김씨 할아버지 65세 채 이틀 남 손가방 현장 검거 그 절도전과 18차례 때문 인생 절반 정도 감옥 가족들 구치소 김씨 할아버지 남 가방 손 버릇 이번 출감 시골마을 고향 농사 여생 시골 전 병원 약 도중 그 남 가방 손 것 도벽 인생 그 평안 마무리 도벽 그 마지막 소망 상습절도 병적도벽인 신앙 대 조세형씨 남 집 담 검거 지금 그 의적 대도 자존심 어리숙한 좀도둑 전락 사람 조씨 이번 범행 세 살 버릇 여 말 그 도둑질 치 습관 도벽 이 수 증명 말 이번 절 사건 고통 인간적 고뇌 한 전문범죄자 행적 존재 조세형 그 도벽 고통 환자 가식적 자신 상습 절도범 도벽 범죄자 것 아니다취재 도중 우리 도벽 고통 호소 사람 의외 고통 심각 확인 수 그 자신 남 물건 죄책감 자신 인생 최근 아이들 남 물건 손 것 고민 부모들 소유개념 명확 아동들 초기도벽 증상 것 도벽 아이 부모들 치료확률 시 아동 청소년기 불구 분노 식 속 소중 시 주변사람들 외면 것 그 상습절도범 자신들 미래 생각 처벌 도벽 치료 수 절 전력 그 형량 것 일반적 단순절도 경우 벌금형 집행유예 경우 상습성 인정 상습절도죄 3년 이상 징역 최고 무기징역 선고 수 상습성 범행 경위 횟수 피해금액 등 가지 요인 결정 재판과정 병 도벽 인정 형 감량 적절 기준 전문적 평 주관적 판단 경우 대부분 이것 법 안전성 공평성 가능성 제도적 도벽 처벌 이외 대안 도벽 사람 차례 중형 처벌해 효과 대안 이번 그것 도벽 죄인 병 도벽 이해 사회적 대처방안 말
정진영 그것이알고싶다 338회 방송내용 제목 대한민국정부 죽음 밀림 국민 방송 2005년 5월7 밤 10시 55분 연출 박상욱 구성 류재은취재팀 입수 베트남 전쟁 당시 한 장 남한 군 포로 장면 속 한국군 군복 포로 2명 모습 전투 중 발생 실종자 포로 베트남 전 한국군 경우 8년 연인원 32 여명 어마어마 

국민 열광 두 젊은이 그라운드 승부사인 박주영 박지성 수 두 젊은이 번 난관 끝 포기 노력 연습 실력 공통점 공 마음 일 거 당연 일 박주영 신드롬 명승부 명장면 월드컵 예선 청소년축구대회 그 명승부 골 국민들 환호 이후 박주영 소재 패러디 인터넷 등장 박주영 응원가 라 것 그 리그 서울 관중수 예전 약 두 배 이 박주영 반응 마디 쿨 주위 반응 아랑 곳하지 자기 일 전형적 신세대 놀이축구 성공 원 그 축구 운동장 엄마 시장 친구 때 축구공 환상적 그 드리볼 때 축구화 맨발 축구 덕분 실력 목표 달성 축구 것 세상 일 축구 축구만 생각 박주영 이전 선수들 코드 축구스타 그 정신적 지주 두 여자 박주영에게 힘 두 여자 사람 아들 기도 어머니 사람 굼벵이 라 별명 그 여자친구 전반 시즌 마지막 경기 열리 7월 10일 이날 박주영 스무번 생일 이날 관중석 선글래스 경기 관전 한 여인 수 박주영 어머니 것 자신 아들 그림자 존재 이날 박주영 여자친구 지갑 자랑 최근 자신 홈페이지 여자친구 사진 공개 그녀 따뜻한 애정 한편 두 사람 사연 이번 첫 공개 박주영 목표 박지성 박주영 꿈 잉글랜드 진출 것 최근 맨체스터 유나이티드팀 한 박지성 그 꿈 박지성 세계 인정 스타 고등학교때 눈 수 프로팀 대학팀 그 지도한 고등학교 감독 평소 분 명지대 감독 박지성 부탁 정도 그 좌절 력 올림픽대표팀 허정무 감독 눈 리그 진출 2002 한일 월드컵 스타 벤치 그라운드 딩크 감독 감독 부임 네덜란드 아인트호벤팀 박지성 한번 위 홈팬들 아시아 실력 수 노골적 야유 그 부진 1년 반 히딩크 감독 비난 그 출장 박지성 세계적 스타 수 맨유팀 퍼거슨 감독 박지성 선택 것 그 녹초 이상 수 때 수 때문 의지 포기 태극전사 피 그 것 이 우려 벤치신세 대 그라운드 장악하 그 꿈 두 젊은이 꿈 것 매순간 노력 한국 축구 역사 두 젊은이 두 청년 꿈 순간 우리 그 인생 축구장 우리 좌절 꿈
국정원 발표 암살가담자 이만수 가명 발표내용 부정 5월 26일 국정원 진실위원회 당시 중앙정보부 파리연수생 신현

...

4월 한 여성 괴성 음성 파일 공개 대한민국 목소리 주인공 1983년 29살 임원 초고속 승진 대한항공 3세 조현민 조현민 전 전무 물벼락 갑질 의혹 제기 재벌 과 갑질 단어 각종 외신 소개 만 한국 재벌 갑질 논란 땅콩 회항 맷값 폭행 수행기사 매뉴얼 등 해 재벌 3세들 갑질 사건 국민들 공분 재벌 3세 갑질 문제 반복 스페셜 재벌 3세 탐구 대한민국 대표 개 개그맨 기 강유미 재벌 3세 민낯 탐구 이 맞선 을 들 목소리 주요 내용 심려 진심 죄송 매체 보도 대한항공 조현민 전 전무 물벼락 갑질 의혹 제기 여기 조현민 전 전무 음성 파일 공개 소문 무성 갑질 실체 이 2014년 땅콩 회항 피해자 박창진 전 대한항공 사무장 당시 증거 증인 난항 중 조현아 전 부사장 1등석 탑승 한 승객 메신저 내용 증거로채택되 박창진 전 사무장 술 힘 미쳤나봐 비행기 출발 뒤 미친X이 사무장 여자 때문 몇 사람 것 1등석 승객 메신저 내용 조현아 전 부사장 항로보안법 위반 등 혐의 구속기소 피고인 진지 성찰 반성 이유 집행유예 선고 사건 실질적 피해자 박창진 전 사무장 조현아 전 부사장 진정한 사과 말 재판 조현아 짓 실소 잡담 잡담 소리 때문 신경질 정도 저 이야길 한마디 경청 적 사람 자기 것 생각 변호사들 힘 막강 생각 박창진 대한항공 전 사무장 재벌 그 재벌 3세 갑질 논란 재벌 갑질 이유 심리적 원인 작용 미국 대학 연구팀 사회 계층 비윤리적 행동 논문 발표 논문 상위계층 운전자들 교통법규 것인가 실험 포함 실험 결과 저렴한 차 사람 최고급 차 운전자들 교통법규 비율 우리나라 사람들 사회 경제적 위치 부도덕 행동 은 미국 연구 토대 흥미로운 실험 진행 충남대 심리학 전우영 교수팀 강남 일대 한 사거리 정상 유턴 불법 유턴 차 가격대 조사 결과 재벌 3세 민낯 재벌 3세 단어 부 권위 부족함 거 것 그 공식 석상 명품 나 인자한 웃음 이 갑질 곳 일정한 특성 사적 공간 집 차 회사 집무실 등 사적 공간 여 민낯 그 옆 시간 운전기사 수행비서 가사도우미 등 일상적 폭언 

진화 공존 갈라파고스 저 3부 불편한 진실 xa0 진화 실험장 갈라파고스 다큐멘터리 방송 태평양 한가운데 고립 갈라파고스는 곳 수 희귀한 동식물 서식지 유명 지금 활화산 연기 화산 바다 곳 생명 행성 황량 속 자연 뿌리 그들 생존전략 삶 영위 열세 개 중심 백여 개 암초 돌섬 갈라파고스 적도 열대 한대 동물 공존 갈라파고스만 희귀종 적도 바다 남극 수 펭귄 세계 바다이구아나 수 최근 종 진화 잡종 이구아나까지 등장 그 고립무원 수 해저 화산 지구 어디 수 창조 갈라파고스 생물들 생존 기록 영상 제 3부 불편한 진실 xa0 3 주민 10 관광객들 xa0 에콰도르 키토 두 시간 정도 것 리 갈라파고스 발트라섬 공항 입국절차 때 외국인 100 에콰도르 국민 6 갈라파고스 주민 무료 입장 황량 모래밭 덩그러 발트라섬 xa0 공항 대부분 갈라파고스 여행 시작 갈라파고스 주민 약 3 명 2천 명 인구 몇 년 사이 그 산타크루즈섬 크리스토발섬 이사벨라섬 그 산타크루즈섬 섬 비행기 모두 이동 가능 거리 곳곳 이구아나 수 해변 물개 여유 자체 동물원 평화 신비 여기 관광책 법 이야기 현실 이 xa0 국립공원 갈라파고스 공사 중관광객들 관광업 종사 이주주민들 시작 턱 부족한 주거시설 갈라파고스섬 곳곳 용암 바위 위 위태 집 시작 건축자재 용암 바위 곳곳 흙 자갈 공급 아이러니하 갈라파고스섬 면적 97 국립공원 지정 곳 국립공원 흙 공사 것 그 주민 관광객 농사 지역 이곳 외래종 갈라파고스 생태계 파괴 갈라파고스 조성 자연 관광객들 자연 파괴 생태 관광 딜레마 해결 길 xa0 섬 주인 누구인가사람 이구아나 갈라파고스거북 바다사자 곳곳 위험 노출 차 위협 누군가 매달아 낚싯줄 올가미 것 리 밤 소음 밤잠 오염 물 쓰레기통 것 이 일상 초식동물 이구아나 쓰레기통 생선내장 뼈 바다사자 해변 바다 관광객들 점령 이곳 이 곳 갈라파고스 위협 적 기후변화도 엘니뇨 사람 그 지
우울증 전 세계적 심각 질환 우을증 초 진단 개입 증상 완화 수 정신 치료 사회적 편견 치료 악화 경우 독립 판 팟

그 피지 낙토 타작마당 비밀하나님 약속 땅 낙토 라 신도들 남태평양 이주 은혜로교회 신옥주 목사 성경 말씀 한국 400 명 신 피지 낙원 건설 피지 탈출 제보자들 그곳 끔찍 경험 제작진 여권 채 12시간 이상 중노동 임금 귀국 외출 자유 수 반감금 상태 것 귀신 영혼 명목 타작마당 진행 이 부모 자식 간 서로 특정 신도 집단폭행 잔혹한 의식 것 익명 제보자 제작진 영상파일 영상 속 그간 공개 신옥주 목사 설교 장면 타작마당 비밀 한편 구속 신 목사 제작진 인터뷰 타작마당 은 자신 지시 것 헌금 이주 신도들 자발적 참여 것 주장 전문가들 가족 간 공개 폭행 의식 목사 신도들 장악하 이주 완성 목적 밀접 분석 신옥주 목사 낙원 정체 무엇인가제작진은 신 목사 주장 낙토 실체 파악 은혜로교회 신도들 노동력 이용 피지 다양 사업 분야 진출 중심 신 목사 아들 씨 대표 그레이스로드 그룹 전역 60개 점포 대규모 정부 사업 참여 만큼 유력 기업체 변신 제작진 신 목사 체포 이후 한국 경찰 경찰 공조 대표 비롯 은혜로교회 간부들 검거 과정 화면 양국 경찰 주요 피의자들 성공적 체포 한국 송환 이유 체포 이틀 뒤 대표 비롯 피의자들 법무부 석방 전역 손 그레이스로드 그룹 실체 무엇 의문 송환 중단 이유 무엇 이번 주 토요일 25일 밤 11시 5분 방송 그것 기간 국내외 추적 신 목사 은혜로교회 실상 신도들 강요 타작마당 비밀 이 피 낙토 의 실체 방송 방송 2018 08 25 밤 11 05연 장경주 글 구성 신진주
운동화 원재료 생산 물류 전 과정 현장 일 사람들 켤레 운동화 삶 발자국 여정 xa0 일상적 소비재 한 켤레 운동화 당신 여정 신용카드 돈 지불 수 생각 운동화 여정 생각 간단 말레이시아 모 고무나무 수액 채취 할아버지 구토 만큼 악취 속 꿈 고무공장 20대 청춘 평생 신발 자부심 하나 손바닥 상처투성이 슬로바키아 운동화 공장 할아버지 결혼 지 달 만 컨테이너선 항해사 세계 각지 사람 손 손 당신 전달 xa0 다큐프라 내 운동화 몇 명 운동화 원재료 최종 유통 생산

세계 지붕 파미르 서식 다양한 야생동물들 생태소개 1부 파미르 서식 다양한 야생동물 파미르의 지역생태 소개 그 최고 포식자인 늑대 중심 생존 현장 늑대 이외 눈표범 마르코폴 양 아이벡스 수염수리 등 다양한 동물들 관계 황량 파미르 지 소개 주요 에피소드 늑대 인간 늑대 야생동물 겨울 가축 공격 양 염소 야크 가축 유목생활 파미르인들에게 두려움 원망 대상 유목민 늑대 이야기 이 적대적 공존관계 세계 최초 최상위 포식자 눈표범 늑대 하나 먹이 신경전 벌 어디 진귀한 광경 야생 숨결 수 단 번 공개 적 비밀 땅 세계 지붕 파미르 n거대산맥들 해발 4 000m 고지 세계 최초 하나 먹이 벌 최상위 포식자 신경전 총 제작기간 2년 추적 잠복 제작진 집요함 대작 xa0 파미르고원 번 적 익숙 이름 국내 소개 적 비밀 땅 파미르고원 히말라야산맥 비롯 텐샨 카라코람 쿤룬 힌두쿠시 산맥 곳 평균 해발고도 4000m 산악 들 히말라야 누구 손길 미지 땅 삭막 땅 발 생명들 소개 자연다큐멘터리 명 답 수 야생동물들 모습 무 카메라 설치 촬영 영상 늑대무리 위계질서 먹이 포식자 면모 수 눈표범 늑대 장면 은 녀석들 제작진 집요함 지 반증 진귀 영상 사냥 마르코폴로양 을 눈표범 대가 전리품 늑대 둘 신경전 포착 촬영 외 아이벡스 야생 염소 마르코폴 산양 수염 수리 등 파미르 서식 다양한 야생동물 생태 밀 다큐 xa0 본방송 2014 06 16 18 밤 9시 50분 n재방송 2014 06 22 밤 8시 15분 3부작 연속 방영 xa0 제작진 제작진 기획 추덕담 연출 xa0 n기획의 xa0 세계 지붕 파미르 고원 한번쯤 적 익숙 이름 국내 소개 바 파미르 텐샨 카라코람 산맥 쿤룬 산맥 등 험준 고산들 지점 형성 고원지대 그 세계 지붕 히말라야 매력 지역 파미르 고원 위치해 타지키스탄 아프가니스탄 파키스탄 키르기스스탄 중국 등 나라들 국경 불안 정세 접근 허락 곳 산악인 도전 히말라야 파미르 누구 손길 미지 땅 곳 평균 해발 4000미터 이상 고산 주변 평원 땅바닥 제 초록빛 수 그 지 

조인성 뉴 논스톱 동창회 이민우 21살 나 것 종영 후 16년 만 뉴 논스톱 동창회 참석 조인성 16년 만 민우 형 38살 조인성 당시 21살 조인성 것 말 조인성 동창회 전 박경림 뉴 논스톱 멤버 누구 질문 민우 형 한 바 이 이민우 나 뉴 논스톱 이후 번 1년 번 며 시간들 오랜만 뉴 논스톱 의 얼굴들 이야기 청춘다큐 스물 2부 공개 조인성 작품 때 마다 단두대 기분 배우 조인성 뉴 논스톱 동창회 자리 동료들 작품 고민 정태우 뉴 논스톱 촬영 당시 아침 9시 대기실 전날 조인성 출연 드라마 시청률 체크 면 당시 조인성 본인 선배 제작진 자신 연기 체크 기억 말 조인성 이 작품 거 수 며 마음 작품 이유 작품 때 단두대 기분 지금 말 수 무리수 노력 이 동료들 모습 지금 조인성 것 이 각자 고민들 며 서로 격려 이민우 은둔 중 스물 이유 사과 배우 이민우 청춘다큐 스물 섭외 이유 1년 6개월 정도 생각 활동 중 이 뉴 논스톱 동료들 제작진 시청자들 미안 얘 말 당시 주변 사람 때문 오해 시작 하차 결정 오해 마지막 날 녹화 며 뉴 논스톱 하차 상황 설명 당시 생각 삶 후회 장면 이민우 사정 무엇 청춘다큐 스물 2부 뒤늦게야 이민우 진심 방송 활동 대 길냥이들 아빠 근황 공개
글로벌 기업 책 총수 줌심 황제 경영 각종 편법 갑질 대표 인성 논란 등 한국 기업문화 오너 중심 리더십 근본적 문제점 한계 상징 한국사회 이 시정 요구 목소리 항공사 오너 일가 편법 불법 의혹 오너 일가 퇴진 요구 구성원 집회 열리 회사 유무형 손해 일 발생 주주들 오너 일 책 자진 책 오너 모습 아이폰 전 세계 휴대폰 시장 선도 스티브 잡스 본인 애플 적 본인 창업 회사 창업주 수 사실 우리 주식회사 모습 점 우리 차이 내 것 글로벌 기업들 창업자 회사 유무형 손해 판단 경우 책 회사 상징 회사 퇴사 퇴사 것 창업자들 마찬가지 애플 창업자 스티브 잡스 끝 때 뒷모습 경우 1년 전 미국 일 세계 각광 스타트업 기업 세계 최대 차량공유업체 우버 우버 창업자 트래비스 칼라닉 2017년 돌연

In [71]:
metadata['n_synop'] = s_nounslist

In [72]:
metadata['n_synop'][0]

'저 목 연쇄살인 공포 부녀 연쇄 피습 사건 진실 방송일시 2004년 7월 03일 밤11시05분 윤 성 작 류 혜 린서울 서남부 지역 반경 4Km 안 2월 5월사이 부녀 피습사건 4건 발생 3명 1명 목숨 지금 경찰 것 금품 성폭행 흔적 사실 범행 동기 불분명 범행수법 잔혹 이유 범죄 조심 추정 인터넷 공포 괴담 지 범인 특정 버스 노선 하얀색 옷 여자 죽 며 근거 소문 확산 서남부지역 주민들 서울판 살인 추억 것 아니냐 불안 동기 범죄 사람 찔렀어요지난 5월 9일 02시 보라매 공원 남문 오솔길 여대생 김모 22 양 졸업 의상 구입 귀가도중 괴한 가슴 옆구리 등 흉기 살해 범행 시간 남자친구 통화한 01시57분10초 59분20초사 2분 10초 김모 22 양 일 것 그녀 마지막 말 사람 피해자 주변 뚜렷 단서 경찰 수사 한달 목요일 새벽 연쇄범죄인 단독범죄인가지난 2월 26일 새벽 신림시장 새벽일하러간 할머니 배웅 여고생 박모 18 양 괴한 흉기 가슴 등 13차례 리 중상 4월22 고척동 여대생 송모 20 양 자신 현관문 열쇠 채 흉기 7차례 사망 5월13 새벽 2시30분 중국교포 한모 39 친구들 술 화장실 흉기 사망 서남부지역 발생 부녀 피습사건 의혹들 속 연쇄범죄 가능성 제 그것 수사전담반 20 간 동행취재 날 복잡해지 다양 범죄 해결하기위한 방법 해외 사례 범죄심리 전문가들 진단'

## tfidf 문서간 거리(유사도)

In [73]:
tfidf = TfidfVectorizer(min_df=10)

# tfidf_matrix : 1890x4396 sparse matrix
tfidf_matrix = tfidf.fit_transform(metadata['n_synop'].values.astype('U'))
documnet_distance = (tfidf_matrix * tfidf_matrix.T)
#문서의 거리 ; cosine_sim = cosine_similarity(tfidf_matrix, tfidf_matrix)

In [74]:
tfidf

TfidfVectorizer(analyzer='word', binary=False, decode_error='strict',
        dtype=<class 'numpy.int64'>, encoding='utf-8', input='content',
        lowercase=True, max_df=1.0, max_features=None, min_df=10,
        ngram_range=(1, 1), norm='l2', preprocessor=None, smooth_idf=True,
        stop_words=None, strip_accents=None, sublinear_tf=False,
        token_pattern='(?u)\\b\\w\\w+\\b', tokenizer=None, use_idf=True,
        vocabulary=None)

## 코사인 유사도 점수 계산

In [75]:
# min_df = 10
print('유사도 분석을 위한 ' + str(documnet_distance.get_shape()[0]) + 'x' + str(documnet_distance.get_shape()[1]) + ' matrix.')
print(documnet_distance.toarray())

유사도 분석을 위한 2747x2747 matrix.
[[1.         0.01853851 0.01429624 ... 0.03054564 0.         0.00419333]
 [0.01853851 1.         0.0767795  ... 0.05500374 0.02194011 0.01011418]
 [0.01429624 0.0767795  1.         ... 0.04541698 0.0658516  0.02002492]
 ...
 [0.03054564 0.05500374 0.04541698 ... 1.         0.01626252 0.00991079]
 [0.         0.02194011 0.0658516  ... 0.01626252 1.         0.00222597]
 [0.00419333 0.01011418 0.02002492 ... 0.00991079 0.00222597 1.        ]]


In [76]:
# min_df=10
cosine_sim = cosine_similarity(tfidf_matrix, tfidf_matrix)
print(cosine_sim)
tfidf_matrix.shape

[[1.         0.01853851 0.01429624 ... 0.03054564 0.         0.00419333]
 [0.01853851 1.         0.0767795  ... 0.05500374 0.02194011 0.01011418]
 [0.01429624 0.0767795  1.         ... 0.04541698 0.0658516  0.02002492]
 ...
 [0.03054564 0.05500374 0.04541698 ... 1.         0.01626252 0.00991079]
 [0.         0.02194011 0.0658516  ... 0.01626252 1.         0.00222597]
 [0.00419333 0.01011418 0.02002492 ... 0.00991079 0.00222597 1.        ]]


(2747, 5838)

In [77]:
# 데이터 셋의 id는 1부터, dataframe의 index는 0부터
#index는 dataframe의 idx
indices = pd.Series(metadata.index, index=metadata['id'])

In [78]:
def get_recommendations(idx, cosine_sim=cosine_sim):
    #제목과 일치하는 에피소드 인덱스 가지고옴
    idx = indices[idx]
    
    sim_scores = list(enumerate(cosine_sim[idx]))
    
    sim_scores = sorted(sim_scores, key=lambda x: x[1], reverse=True)
    
    #비슷한 에피소드 상위 10개
    sim_scores = sim_scores[1:11]
    
    # indices
    epi_indices = [i[0] for i in sim_scores]
    
        
    return metadata['epi'].iloc[epi_indices]

In [79]:
metadata['epi'][1]

'2004 행복 신드롬 - 당신은 웰빙하고 계십니까'

In [80]:
# index - id 불일치
get_recommendations(1)

227              잡거나 혹은 잡히거나 - '경찰범죄'와의 전쟁
977                          무죄인가? 무기징역인가?
2241       비밀친구와 살인 시나리오 - 인천 여아 살해 사건의 진실
640     한인 살해범은 잡히지 않는다 - 워싱턴DC 미제 살인사건 13
356                  연쇄성폭행범, 보일러 발바리를 잡아라.
1714              비극의 상견례 - 죽음의 불청객은 누구인가?
511     미스터리, 청산가리 막걸리 살인사건-아버지와 딸은 공범이었나?
2159                  죽은 내 동생은 만취 여성이 아닙니다
2182          범인은 섬 안에 있다? - 평일도 살인사건 미스터리
3                           살인마는 바로 곁에 있었다
Name: epi, dtype: object

In [81]:
print('episode : ' + metadata['epi'][236])
get_recommendations(236, cosine_sim)

episode : 남측 벼를 심으려 왔습니다 - 평양, 당곡리에서 맺은 결실


251             숭례문 미스터리 - 그래도 남는 의혹의 실체
2456                천장 속의 비밀 -제천 화재 미스터리
25           방문객은 누구인가- 서천 Y카센터 사건의 미스터리
1659         화염 속의 진실게임- 가면 쓴 방화범은 누구인가?
818             5년간의 공포, 용탄리 연쇄 방화범을 잡아라
1299                              위험한 가족
953     기이한 마을, 이상한 실종 - 서천 기동슈퍼 화재 미스터리
376                   무너진 망루 - 용산참사를 말한다
385           죽이고 싶어 죽였다?! - 강호순 살인 미스터리
858                  진실을 밝히는 칼, 국과수는 말한다
Name: epi, dtype: object

## Recommender  

In [82]:
def recommender(idx):
    print('episode :'+ str(idx) + ' / ' + metadata['epi'][idx-1])
    
    return get_recommendations(idx, cosine_sim)
    

## 전체 데이터 추천 확인

In [83]:
for i in metadata['id']:
    print(recommender(i))
    print('')

episode :1 / 되살아난 연쇄살인의 공포 - 부녀자 연쇄 피습 사건의 진실
227              잡거나 혹은 잡히거나 - '경찰범죄'와의 전쟁
977                          무죄인가? 무기징역인가?
2241       비밀친구와 살인 시나리오 - 인천 여아 살해 사건의 진실
640     한인 살해범은 잡히지 않는다 - 워싱턴DC 미제 살인사건 13
356                  연쇄성폭행범, 보일러 발바리를 잡아라.
1714              비극의 상견례 - 죽음의 불청객은 누구인가?
511     미스터리, 청산가리 막걸리 살인사건-아버지와 딸은 공범이었나?
2159                  죽은 내 동생은 만취 여성이 아닙니다
2182          범인은 섬 안에 있다? - 평일도 살인사건 미스터리
3                           살인마는 바로 곁에 있었다
Name: epi, dtype: object

episode :2 / 2004 행복 신드롬 - 당신은 웰빙하고 계십니까
1475                    유기농, 생명의 식탁을 차리다
181                    0.2평의 기적, 절하는 사람들
1111                   자본주의 2부. 소비는 감정이다
1782                 밥상! 상식을 뒤집다. 채식의 함정
1244      인간탐구 욕망 호모 컨슈머리쿠스 제1부-내가 사는 이유
134            빛에 관한 보고서 - 독이 되고 약이 되는 빛
835                        잠 - 3부 잠의 경쟁력
88                            혼자 밥먹는 사람들
1245    인간탐구 욕망 호모 컨슈머리쿠스 제2부-소비중추를 자극하라
547         생명의 선택 1부 - 당신이 먹는 게 삼대를 간다.
Name: epi, dtype: object

episode :3 / 500회 특집 

Name: epi, dtype: object

episode :23 / 누가 육영수 여사를 쏘았는가 - 8.15 저격사건, 30년간의 의혹
28      누가 육영수 여사를 쏘았는가 2  -  나는 육영수 여사를 겨냥하지 않았다
616               나는 여동생을 쏘지 않았다 - 정인숙 피살 사건 미스터리
2101                    작전; 설계된 게임 - '디도스 사건'의 비밀
2060             죽거나 혹은, 죽이거나 - VIP 5촌 간 살인사건의 진실
651             아버지의 끝나지 않은 전쟁-JSA 김훈 중위 죽음의 미스터리
2342                 140억은 누구의 돈인가? -BBK 투자금 진실게임
1998             자백과 고백, 그리고 거짓말 - ‘엄궁동 2인조 사건’의 
713                             1부 - 타블로, 스탠퍼드 가다
2120                     무대 위의 암살 - 김정남 피살사건 미스터리
2198                      대통령의 금고 - 수인번호 503번의 비밀
Name: epi, dtype: object

episode :24 / 대한민국은 그들의 천국인가 - 금발에 파란 눈, 외국인 강사 실태보고
2382                            <꿈, 떠나다>
147                  단일민족의 나라, 당신들의 대한민국
588     스타강사와 욕망의 늪 - 그들은 왜 시험지를 훔치려 했나?
1606                       노아의 방주를 탄 사람들
1602              한국인과 영어 2부 조선, 영어를 만나다
2356            ‘괜찮아 디바인’ 1부 코리안 스타일 오케이
2359              ‘괜찮아 디바인’ 2부 낯선 시간 속에서
1600              한국인과 영어 1부 욕망의 언어 잉글리시
1603           

Name: epi, dtype: object

episode :42 / 꿈을 쏘다! - 박주영 박지성
422                                         당신은 박지성을 아는가
2483                                    영화감독 김기덕  거장의 민낯
545                                   추신수, 마침내 메이저리그를 치다
1655                                      슈틸리케, 리더십을 부탁해
92                                 ‘D-103, 축구 국가대표 전훈기록’
647                  27.5%의 확률게임- 대한민국은 월드컵 16강에 오를 것인가?
1351                                       나는 홈리스월드컵에 간다
1968                           리우올림픽 특집 박세리, 내 생에 최고의 순간
692     <2010 MBC 현대사 연속 기획>경술국치 100년 특집“축구 그리고 세 개의 조국”
1301                                              감독 봉준호
Name: epi, dtype: object

episode :43 / 암살자들의 고백 - 내가 김형욱을 죽였다
2106    작전; 설계된 게임 - “5163부대의 위험한 충성”
2381     유서가 된 2G폰의 증언 - 국정원 변호사 사망의혹
2334              은밀하게 꼼꼼하게 -각하의 비밀부대
1809                내부고발자  그들의 외로운 고백
2053     두 개의 밀실 - 세월호 화물칸과 연안부두 205호
2428                        국정원과 가짜보수
2084                은밀한 폭력  문화계 블랙리스트
2398                    MBC몰락  7년의 기록
2407  

Name: epi, dtype: object

episode :65 / 엄마 도와 주세요 - 어른이 될 수 없는 어른들
1936                제 1부. 착한 내 딸의 반란
1941                 제 2부. 엄마처럼 안 살아
433        엄마는 무엇으로 사는가 - 고백2. 엄마의 방
432        엄마는 무엇으로 사는가 - 고백1. 엄마의 힘
434      엄마는 무엇으로 사는가 - 고백3. 엄마의 짝사랑
402     모성탐구 엄마가 달라졌어요 제1편 초보엄마 아카데미
569              2009 가장 슬픈이야기, 풀빵엄마
403        모성탐구 엄마가 달라졌어요 제2편 엄마 바꾸기
223         위험한 엄마들  “나는 내 아기를 미워한다”
1004                마더 쇼크 1부 모성의 대물림
Name: epi, dtype: object

episode :66 / 서바이벌 - 고지마 원숭이 5년의 기록
508                            유혹의 기술
2653    원령공주의 땅 야쿠시마 - 2부 원숭이와 사슴의 왕국
2436         <생명의 전략 번식> 제2부 - 은밀한 전쟁
2435            <생명의 전략 번식> 1부 끝없는 선택
519      동과 서 제2편 서양인은 보려하고 동양인은 되려한다
2673                    숲 속의 인간, 오랑우탄
444                           동물원 이야기
605                           도시의 유인원
2189                           권력의 탄생
2654    원령공주의 땅 야쿠시마 - 3부 섬이 나를 놓지 않네
Name: epi, dtype: object

episode :67 / 노인을 팝니다 - 효친원의 빗나간 효심
1819              소문과 거짓말 - 미인도 스캔들
209                    

Name: epi, dtype: object

episode :90 / 내 재산 누가 지켜 주나요 - 치매 노인의 재산권 보호
983         치매를 부탁해 - 1부 어느날 갑자기
1064      치매를 부탁해2- 1부  나는 치매입니다
1071       치매를 부탁해2- 6부-치매 앞의 당신
1744    가족끼리 왜이래? 부모의 몫 VS 자식의 몫
26         상속분쟁, 자식에게 재앙을 물려준 부모
1460        치매를 부탁해2-1부 나는 치매입니다
1066      치매를 부탁해2-  3부 치매라도 괜찮아
1462       치매를 부탁해2- 6부-치매 앞의 당신
1461       치매를 부탁해2- 3부 치매라도 괜찮아
2307               치매와 함께 사는 사람들
Name: epi, dtype: object

episode :91 / 이제는 웃다가 성공한다 - 진수테리 fun경영 공개특강
2323                당신 곁의 까레이스키
1923       최고의 기업의 성공전략사람에 집중하라
366                       유머 1부
629     당신의 성격 3부 나는 내성적인 사람입니다
370                       유머 2부
1898              누가 혁신을 주도하는가?
2280    한번뿐인 인생! 당신은 욜로(YOLO)족?
780          2011 신년특집 안철수와 박경철
2743                  CEO 사표 쓰다
496             당신의 다음 차는 무엇입니까
Name: epi, dtype: object

episode :92 / 유전무죄 무전유죄, 변호인의 도움은 가진자 만의 특권인가
333                           셜록 홈즈를 원하는 사람들 - 사립탐정 논란
1390                              죽음의 조종자 - 가면 쓴 소시오패스
551                       

...

1707       감각의 제국 4부 봄(seeing)의 기적
1709              감각의 제국 5부 퍼펙트 센스
1701    감각의 제국 1부 살아 있는 모든 것은 감각한다
1703           감각의 제국 2부 오감의 흔적, 뇌
1704         감각의 제국 3부 감각의 변주곡, 기억
1710          감각의 제국 6부 이기적 본능, 공감
282                인터뷰다큐 성장통, '나이'
571                   승일 스토리 나는 산다
1386                      작심 1만 시간
2376             천국의 새 - 1부 다리없는 새
Name: epi, dtype: object

episode :2379 / 천국의 새 - 3부 새 그리고 사람들
796         사냥의기술 2부 새, 대지를 응시하다.
1681      사냥의기술 2부 - 새, 대지를 응시하다-
560           라이온 퀸 - 1부 초원의 여전사들
681       여름방학특집 <헌터스 - 야생의 추격자들>
795           사냥의기술 1부 새, 물을 이기다.
1680        사냥의기술 1부 - 새, 물을 이기다-
2669            <밤의 제국> 1부 밤의 지배자
1990    다큐프라임 <모멘트> 1부 영원과 순간의 사이
562             라이온 퀸 - 2부 위대한 유산
650                     매를 가진 사람들
Name: epi, dtype: object

episode :2380 / 종가시절 宗家時節
1384                   이영애의 만찬 2부
1739            맛이란 무엇인가 2부 맛의 기억
2242         옴니버스食 다큐멘터리 더 잘 먹는 법
1383                   이영애의 만찬 1부
707                방랑식객 5. 일본을 가다
556     생명의 선택 3부 - 페어푸드 

Name: epi, dtype: object

episode :2422 / 스텔라데이지호  국가의 침몰
2228    그 바다에 사람이 있다 - ‘스텔라 데이지’호 침몰 Day6
1426      희망은 왜 가라앉았나? - ‘세월호 침몰’의 불편한 진실
2556                     로그북 세월호 잠수사들의 일기
1870    세타(Θ)의 경고! 경고!  - 세월호와 205호 그리고 비
847                         만균 씨의 지워진 25년
1452                    세월호 참사의 불편한 진실 2부
289                  어느 재력가의 필리핀 피살 미스터리 
2499      사탕수수밭 살인사건의 비밀 - 138억은 어디로 사라졌나
1175          누군가는 알고 있다 - 필리핀 연쇄 납치 미스터리
33                 대한민국정부-죽음의 밀림에 국민을 버리다
Name: epi, dtype: object

episode :2423 / 천불천탑의 신비 미얀마 - 2부 버강, 위대한 왕국의 꿈
1675     천불천탑의 신비 미얀마 - 3부 미얀마, 비밀의 첫 장을 열다
2416               천불천탑의 신비 미얀마 - 1부 황금의 전설
334                        물위를 떠도는 영혼 바다 집시
2370                불멸의 마야 - 1부 옥수수 문명을 찾아서
1648      EBS 특별기획 다큐멘터리 - 위대한 바빌론 제3부 공중정원
871            인류문명탐험-1부 사라진 고대무역도시, 인더스 문명
2371                불멸의 마야 - 2부 260일 달력, 촐낀
1647       EBS 특별기획 다큐멘터리 - 위대한 바빌론 제2부 바벨탑
1645    EBS 특별기획 다큐멘터리 - 위대한 바빌론 제1부 바빌론 시티
2322             <불멸의 진시황> 2부 영원한 제국 - 진시황릉
Name: ep

Name: epi, dtype: object

episode :2511 / 돈, 왜 쓰나요?
1244      인간탐구 욕망 호모 컨슈머리쿠스 제1부-내가 사는 이유
1111                   자본주의 2부. 소비는 감정이다
1245    인간탐구 욕망 호모 컨슈머리쿠스 제2부-소비중추를 자극하라
677                             지름신을 부탁해
1950    저성장시대에 살아남기 - 1부 텅 빈 지갑, 쓸 돈이 없다
163                         내가 도시를 떠난 이유
119                SBS 스페셜 집에서 집(家)을 찾는다
615                          남자의 말 여자의 말
1956          저성장시대에 살아남기 - 2부 인구절벽을 넘어라
985                    “나는 산다 - 오복식 고물상”
Name: epi, dtype: object

episode :2512 / 봄 마중 80km - 경춘선 전철
2511               봄 마중 80km - 경춘선 전철
2668                 당신이 잠든사이 - 올빼미버스
2283          힘내라 미라클 - 독립 야구단 연천 미라클
2689    혼저옵서예 그만옵서예 - 2018년 여름 제주국제공항
2723        그 섬이 꿈꾸는 풍경 - 전라남도 고흥 연홍도
2543           세월을 두드리다 - 부산 영도 깡깡이마을
2532         온다(Onda) 꼬레아 - 뮤직뱅크 인 칠레
2553            135번째 봄 - 진수중앙시장 72시간
2314          출동 여름바다를 지켜라 - 영종도 해양경찰
2479                 꽃길만 걸어요 - 남사화훼단지
Name: epi, dtype: object

episode :2513 / 900개의 영혼,파푸아뉴기니 1부 화산섬, 마투핏
1885                   화산 1


episode :2588 / 회장님의 부귀영화
1641     아파트 중독-3부 우리는 왜 아파트에 사는가
1640           아파트 중독-2부 시간이 만든 집
1884        완장의 자격 - 입주자 대표가 뭐길래!
1638             아파트 중독-1부 공간의 발견
1768               아파트, 혼란의 시장 2부
1765                  아파트, 혼란의 시장
2526              누가 아파트 가격을 올리는가
2540           고립된 섬, 아파트 단지를 구하라
2455               나는 비정규직 경비원입니다
1123    기묘한 실종 - 사라진 회장님과 2,200억 
Name: epi, dtype: object

episode :2589 / <뼈> 3부 뼈는 살아있다
2586             <뼈> 2부 뼈, 아주 오래된 질문들
2585               <뼈> 1부 뼈, 남겨진 모든 것
1990        다큐프라임 <모멘트> 1부 영원과 순간의 사이
1628                 의학, 동과 서 - 2부 고통
590                     생명 1부 기적의 아이들
1627                 의학, 동과 서 - 1부 시선
1629                 의학, 동과 서 - 3부 의사
1748     우리 WE, 3부 우리는 왜 우리가 되지 못하는가?
606                     산에서 암을 이긴 사람들
1992    다큐프라임 <모멘트> 2부 지나간 것과 올 것의 사이
Name: epi, dtype: object

episode :2590 / 미래 혁명 스마트 팜(2) - 식물 공장
2171                      나의 빛나는 흑역사
2258                     성신제의 달콤한 인생
1153                 우리 학교는 ‘한국 스타일’
1934                


episode :2740 / 남북정상회담 특집 1부 <평화의 맛>
2565    남북정상회담 특집 SBS스페셜 - 여섯 개의 봄
2562                   한반도 평화 오디세이
2745         평양 2박 3일 - 남북정상회담 동행기
2615                   북미정상회담 막전막후
2504         한반도 피스 메이커 - 대전환의 한 달
2650     <옥류관 서울 1호점> 1부 평양냉면 제일일세
2619      세기의 담판 D-4한반도 평화의 문은 열리나
2635         평화가 길입니다 - 임진각 DMZ 투어
2628          북미정상회담 - 평화를 향한 첫 걸음
2240                    한반도의 평화 조건
Name: epi, dtype: object

episode :2741 / 추석 특집 2부 <고향의 맛>
855                         나의 살던 고향은
380                        생존 열차 중국 호
2543           세월을 두드리다 - 부산 영도 깡깡이마을
1384                       이영애의 만찬 2부
1739                맛이란 무엇인가 2부 맛의 기억
2707    이산가족 상봉 특집 <옥류관 서울 1호점> 3부 이산
2242             옴니버스食 다큐멘터리 더 잘 먹는 법
2306                     쇼 돌고래의 슬픈 진실
1491                    댁의 밥상, 안녕하십니까
2712                  당신의 음식값, 만족하십니까
Name: epi, dtype: object

episode :2742 / 청춘다큐 다시, 스물 ? 뉴 논스톱 편 1부
2742             청춘다큐 다시, 스물 - 뉴 논스톱 편 2부
815                               태희의 재발견
2439     하얀거탑 리마스터드 방영

## ==== 추천 시스템  ====

In [84]:
def get_recommendations(idx, cosine_sim=cosine_sim):
    #제목과 일치하는 에피소드 인덱스 가지고옴
    idx = indices[idx]
    
    sim_scores = list(enumerate(cosine_sim[idx]))
    
    sim_scores = sorted(sim_scores, key=lambda x: x[1], reverse=True)
    
    #비슷한 에피소드 상위 10개
    sim_scores = sim_scores[1:11]
    
    # indices
    epi_indices = [i[0] for i in sim_scores]
    print(epi_indices)
    get_result(idx,epi_indices)
    return metadata['epi'].iloc[epi_indices]

In [85]:
result_data = []
def get_result(idx, epi_indices):
    recom_set = epi_indices.copy()
    recom_set = [ x+1 for x in recom_set ]
    recom_set.insert(0, idx+1)
    print(recom_set)
    result_data.append(recom_set)

In [86]:
size = metadata.shape[0]
for i in range(1,size+1):
    get_recommendations(i)
    print('\n')

[227, 977, 2241, 640, 356, 1714, 511, 2159, 2182, 3]
[1, 228, 978, 2242, 641, 357, 1715, 512, 2160, 2183, 4]


[1475, 181, 1111, 1782, 1244, 134, 835, 88, 1245, 547]
[2, 1476, 182, 1112, 1783, 1245, 135, 836, 89, 1246, 548]


[1123, 2425, 712, 283, 1976, 1548, 1665, 2046, 2162, 1984]
[3, 1124, 2426, 713, 284, 1977, 1549, 1666, 2047, 2163, 1985]


[2241, 1917, 206, 2159, 1033, 1196, 265, 0, 385, 8]
[4, 2242, 1918, 207, 2160, 1034, 1197, 266, 1, 386, 9]


[428, 93, 1004, 1005, 1006, 223, 244, 532, 1941, 988]
[5, 429, 94, 1005, 1006, 1007, 224, 245, 533, 1942, 989]


[1198, 564, 992, 566, 1117, 1805, 1150, 1145, 1031, 1039]
[6, 1199, 565, 993, 567, 1118, 1806, 1151, 1146, 1032, 1040]


[177, 721, 242, 692, 934, 128, 1289, 1497, 1500, 258]
[7, 178, 722, 243, 693, 935, 129, 1290, 1498, 1501, 259]


[227, 1942, 2163, 491, 1196, 87, 2324, 231, 883, 376]
[8, 228, 1943, 2164, 492, 1197, 88, 2325, 232, 884, 377]


[1917, 1505, 1742, 2664, 1797, 1060, 2737, 910, 69, 59]
[9, 1918, 1506, 1743, 2665

[1643, 2379, 1115, 5, 589, 137, 1275, 431, 15, 2266]
[73, 1644, 2380, 1116, 6, 590, 138, 1276, 432, 16, 2267]


[1874, 100, 1172, 1177, 1176, 468, 512, 1221, 1174, 1223]
[74, 1875, 101, 1173, 1178, 1177, 469, 513, 1222, 1175, 1224]


[75, 394, 389, 395, 388, 2176, 390, 393, 451, 2664]
[75, 76, 395, 390, 396, 389, 2177, 391, 394, 452, 2665]


[75, 394, 389, 395, 388, 2176, 390, 393, 451, 2664]
[76, 76, 395, 390, 396, 389, 2177, 391, 394, 452, 2665]


[1872, 1762, 1706, 1288, 936, 804, 1125, 503, 2603, 37]
[77, 1873, 1763, 1707, 1289, 937, 805, 1126, 504, 2604, 38]


[79, 33, 1964, 1965, 1963, 2327, 94, 95, 143, 773]
[78, 80, 34, 1965, 1966, 1964, 2328, 95, 96, 144, 774]


[289, 2499, 1175, 487, 2548, 914, 1687, 377, 1250, 505]
[79, 290, 2500, 1176, 488, 2549, 915, 1688, 378, 1251, 506]


[79, 33, 1964, 1965, 1963, 2327, 94, 95, 143, 773]
[80, 80, 34, 1965, 1966, 1964, 2328, 95, 96, 144, 774]


[1791, 1792, 1057, 612, 1660, 164, 81, 2457, 82, 1776]
[81, 1792, 1793, 1058, 613, 1661, 165, 


[229, 857, 1110, 1052, 727, 833, 219, 18, 1946, 54]
[168, 230, 858, 1111, 1053, 728, 834, 220, 19, 1947, 55]


[2196, 2095, 967, 854, 658, 2012, 325, 2212, 1044, 1349]
[169, 2197, 2096, 968, 855, 659, 2013, 326, 2213, 1045, 1350]


[342, 731, 1933, 1633, 198, 1772, 1718, 406, 732, 1818]
[170, 343, 732, 1934, 1634, 199, 1773, 1719, 407, 733, 1819]


[501, 1584, 1466, 1113, 1363, 1322, 1106, 625, 1467, 1362]
[171, 502, 1585, 1467, 1114, 1364, 1323, 1107, 626, 1468, 1363]


[706, 177, 667, 85, 785, 1721, 2014, 503, 2347, 2212]
[172, 707, 178, 668, 86, 786, 1722, 2015, 504, 2348, 2213]


[2024, 233, 2597, 1641, 828, 827, 826, 1640, 1258, 1638]
[173, 2025, 234, 2598, 1642, 829, 828, 827, 1641, 1259, 1639]


[175, 542, 1297, 259, 266, 142, 144, 2391, 1679, 1593]
[174, 176, 543, 1298, 260, 267, 143, 145, 2392, 1680, 1594]


[1332, 1782, 88, 1479, 1740, 2208, 926, 2315, 514, 1912]
[175, 1333, 1783, 89, 1480, 1741, 2209, 927, 2316, 515, 1913]


[259, 266, 173, 1088, 311, 2134, 873, 1188, 2391,

[1882, 2262, 62, 110, 356, 118, 3, 1917, 111, 2297]
[266, 1883, 2263, 63, 111, 357, 119, 4, 1918, 112, 2298]


[259, 175, 173, 1302, 1306, 2027, 1298, 325, 672, 673]
[267, 260, 176, 174, 1303, 1307, 2028, 1299, 326, 673, 674]


[270, 268, 269, 271, 478, 1591, 2693, 95, 2727, 2133]
[268, 271, 269, 270, 272, 479, 1592, 2694, 96, 2728, 2134]


[270, 269, 271, 267, 1591, 478, 2693, 95, 2133, 1951]
[269, 271, 270, 272, 268, 1592, 479, 2694, 96, 2134, 1952]


[270, 268, 271, 267, 1591, 478, 2693, 477, 95, 560]
[270, 271, 269, 272, 268, 1592, 479, 2694, 478, 96, 561]


[268, 269, 271, 267, 1591, 478, 2693, 95, 477, 560]
[271, 269, 270, 272, 268, 1592, 479, 2694, 96, 478, 561]


[270, 269, 268, 267, 1591, 478, 2693, 477, 560, 95]
[272, 271, 270, 269, 268, 1592, 479, 2694, 478, 561, 96]


[50, 792, 1412, 714, 777, 1823, 851, 303, 301, 994]
[273, 51, 793, 1413, 715, 778, 1824, 852, 304, 302, 995]


[1240, 452, 123, 451, 2269, 450, 756, 550, 1235, 496]
[274, 1241, 453, 124, 452, 2270, 451, 757, 5



[501, 499, 976, 1322, 912, 729, 2494, 2501, 913, 175]
[501, 502, 500, 977, 1323, 913, 730, 2495, 2502, 914, 176]


[500, 499, 1186, 1322, 1182, 1188, 1183, 1184, 1187, 1584]
[502, 501, 500, 1187, 1323, 1183, 1189, 1184, 1185, 1188, 1585]


[1038, 2353, 947, 952, 545, 304, 1267, 2603, 220, 667]
[503, 1039, 2354, 948, 953, 546, 305, 1268, 2604, 221, 668]


[1762, 1706, 1872, 13, 1125, 230, 93, 37, 2603, 810]
[504, 1763, 1707, 1873, 14, 1126, 231, 94, 38, 2604, 811]


[656, 561, 810, 2138, 786, 90, 1856, 2488, 2199, 2212]
[505, 657, 562, 811, 2139, 787, 91, 1857, 2489, 2200, 2213]


[2660, 506, 2662, 507, 2663, 912, 911, 2516, 499, 2514]
[506, 2661, 507, 2663, 508, 2664, 913, 912, 2517, 500, 2515]


[2662, 505, 2660, 507, 2663, 1263, 334, 708, 683, 625]
[507, 2663, 506, 2661, 508, 2664, 1264, 335, 709, 684, 626]


[2663, 505, 2660, 506, 2662, 912, 2516, 2514, 499, 2463]
[508, 2664, 506, 2661, 507, 2663, 913, 2517, 2515, 500, 2464]


[65, 2436, 2430, 2435, 1745, 1747, 774, 775, 1992, 605

...

[409, 408, 2005, 1369, 1040, 2004, 163, 1207, 2006, 2284]
[1915, 410, 409, 2006, 1370, 1041, 2005, 164, 1208, 2007, 2285]


[1272, 1654, 1051, 858, 469, 1993, 105, 2145, 1294, 1474]
[1916, 1273, 1655, 1052, 859, 470, 1994, 106, 2146, 1295, 1475]


[1568, 137, 1982, 1508, 1771, 1740, 1535, 1636, 1018, 1090]
[1917, 1569, 138, 1983, 1509, 1772, 1741, 1536, 1637, 1019, 1091]


[2159, 1742, 1505, 2019, 8, 910, 59, 1797, 2664, 198]
[1918, 2160, 1743, 1506, 2020, 9, 911, 60, 1798, 2665, 199]


[2238, 2155, 1480, 955, 1197, 1144, 2087, 1561, 2079, 2162]
[1919, 2239, 2156, 1481, 956, 1198, 1145, 2088, 1562, 2080, 2163]


[1556, 817, 641, 2301, 661, 663, 2649, 662, 1534, 1569]
[1920, 1557, 818, 642, 2302, 662, 664, 2650, 663, 1535, 1570]


[560, 2306, 429, 444, 562, 2471, 2127, 2097, 1316, 2473]
[1921, 561, 2307, 430, 445, 563, 2472, 2128, 2098, 1317, 2474]


[1347, 1345, 1814, 726, 2242, 2204, 1899, 1375, 2018, 1877]
[1922, 1348, 1346, 1815, 727, 2243, 2205, 1900, 1376, 2019, 1878]


[1139, 114

[2163, 194, 199, 3, 2552, 1743, 1634, 86, 322, 2020, 284]


[227, 7, 2074, 2189, 491, 376, 2671, 883, 1654, 2146]
[2164, 228, 8, 2075, 2190, 492, 377, 2672, 884, 1655, 2147]


[2300, 2477, 1464, 2003, 1479, 1804, 2206, 2144, 2461, 2309]
[2165, 2301, 2478, 1465, 2004, 1480, 1805, 2207, 2145, 2462, 2310]


[988, 428, 1439, 4, 532, 1837, 93, 244, 2584, 112]
[2166, 989, 429, 1440, 5, 533, 1838, 94, 245, 2585, 113]


[2020, 1721, 2151, 120, 2014, 1719, 2347, 1722, 2004, 1034]
[2167, 2021, 1722, 2152, 121, 2015, 1720, 2348, 1723, 2005, 1035]


[986, 1460, 1461, 983, 1462, 1070, 1064, 1066, 1071, 1069]
[2168, 987, 1461, 1462, 984, 1463, 1071, 1065, 1067, 1072, 1070]


[1, 2, 3, 4, 5, 6, 7, 8, 9, 10]
[2169, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11]


[2153, 2110, 1052, 738, 2155, 2551, 2721, 2341, 732, 782]
[2170, 2154, 2111, 1053, 739, 2156, 2552, 2722, 2342, 733, 783]


[2053, 1426, 2177, 1452, 2564, 2556, 2121, 2604, 1870, 2570]
[2171, 2054, 1427, 2178, 1453, 2565, 2557, 2122, 2605, 1871, 2571]


[22


[2325, 1343, 753, 1894, 1615, 1621, 2025, 155, 1224, 1223]
[2330, 2326, 1344, 754, 1895, 1616, 1622, 2026, 156, 1225, 1224]


[2331, 2332, 2396, 2397, 2484, 2481, 2181, 1720, 2482, 2022]
[2331, 2332, 2333, 2397, 2398, 2485, 2482, 2182, 1721, 2483, 2023]


[2332, 2330, 2396, 2397, 1622, 2223, 1411, 1449, 1423, 1425]
[2332, 2333, 2331, 2397, 2398, 1623, 2224, 1412, 1450, 1424, 1426]


[2331, 2330, 2396, 2397, 1622, 2223, 2213, 1411, 1449, 1423]
[2333, 2332, 2331, 2397, 2398, 1623, 2224, 2214, 1412, 1450, 1424]


[2185, 2696, 1589, 1798, 601, 2627, 1853, 2679, 887, 2538]
[2334, 2186, 2697, 1590, 1799, 602, 2628, 1854, 2680, 888, 2539]


[2106, 2381, 42, 2428, 2084, 2407, 2398, 2189, 2053, 2358]
[2335, 2107, 2382, 43, 2429, 2085, 2408, 2399, 2190, 2054, 2359]


[2667, 606, 2229, 855, 359, 638, 2677, 391, 1570, 1254]
[2336, 2668, 607, 2230, 856, 360, 639, 2678, 392, 1571, 1255]


[2338, 2345, 2344, 2337, 1425, 1423, 1449, 1447, 1448, 1424]
[2337, 2339, 2346, 2345, 2338, 1426, 1424, 1450, 1

[2496, 330, 2665, 75, 76, 390, 395, 1671, 391, 452, 709]


[2387, 2129, 1882, 985, 1543, 1829, 1948, 1839, 394, 709]
[2497, 2388, 2130, 1883, 986, 1544, 1830, 1949, 1840, 395, 710]


[2518, 2549, 2116, 689, 2126, 1950, 70, 2724, 684, 2645]
[2498, 2519, 2550, 2117, 690, 2127, 1951, 71, 2725, 685, 2646]


[1322, 2382, 316, 85, 579, 96, 716, 2261, 740, 739]
[2499, 1323, 2383, 317, 86, 580, 97, 717, 2262, 741, 740]


[289, 1175, 1250, 1687, 914, 78, 1089, 377, 2324, 2293]
[2500, 290, 1176, 1251, 1688, 915, 79, 1090, 378, 2325, 2294]


[2454, 2450, 2511, 2113, 894, 2668, 2531, 2283, 2689, 2723]
[2501, 2455, 2451, 2512, 2114, 895, 2669, 2532, 2284, 2690, 2724]


[2494, 2490, 2492, 1046, 1375, 816, 2384, 1316, 2363, 2482]
[2502, 2495, 2491, 2493, 1047, 1376, 817, 2385, 1317, 2364, 2483]


[2424, 2493, 349, 2713, 115, 2394, 2166, 2299, 326, 2037]
[2503, 2425, 2494, 350, 2714, 116, 2395, 2167, 2300, 327, 2038]


[2505, 2692, 774, 775, 447, 708, 889, 2690, 625, 691]
[2504, 2506, 2693, 775, 776, 


[2662, 505, 2660, 507, 2663, 1263, 334, 708, 683, 625]
[2663, 2663, 506, 2661, 508, 2664, 1264, 335, 709, 684, 626]


[507, 505, 2660, 506, 2662, 912, 2516, 2514, 499, 903]
[2664, 508, 506, 2661, 507, 2663, 913, 2517, 2515, 500, 904]


[389, 74, 75, 394, 450, 1917, 910, 1505, 1742, 8]
[2665, 390, 75, 76, 395, 451, 1918, 911, 1506, 1743, 9]


[85, 354, 2491, 2701, 999, 2080, 2135, 2413, 2108, 678]
[2666, 86, 355, 2492, 2702, 1000, 2081, 2136, 2414, 2109, 679]


[2281, 378, 2520, 2499, 2060, 2657, 194, 640, 2610, 567]
[2667, 2282, 379, 2521, 2500, 2061, 2658, 195, 641, 2611, 568]


[2335, 2677, 1140, 1050, 243, 174, 81, 63, 876, 1460]
[2668, 2336, 2678, 1141, 1051, 244, 175, 82, 64, 877, 1461]


[2450, 2511, 2283, 2689, 2323, 2723, 2543, 2532, 2553, 2314]
[2669, 2451, 2512, 2284, 2690, 2324, 2724, 2544, 2533, 2554, 2315]


[2672, 1992, 796, 1681, 795, 1680, 2378, 681, 560, 562]
[2670, 2673, 1993, 797, 1682, 796, 1681, 2379, 682, 561, 563]


[616, 203, 215, 2096, 484, 862, 2544, 498, 132

In [87]:
index_name = ['id']
for i in range(10):
    index_name.append('reco'+str(i+1))
index_name

['id',
 'reco1',
 'reco2',
 'reco3',
 'reco4',
 'reco5',
 'reco6',
 'reco7',
 'reco8',
 'reco9',
 'reco10']

In [88]:
df_result = pd.DataFrame(result_data, columns = index_name)
df_result

id  reco1  reco2  reco3  reco4  reco5  reco6  reco7  reco8  reco9  \
0        1    228    978   2242    641    357   1715    512   2160   2183   
1        2   1476    182   1112   1783   1245    135    836     89   1246   
2        3   1124   2426    713    284   1977   1549   1666   2047   2163   
3        4   2242   1918    207   2160   1034   1197    266      1    386   
4        5    429     94   1005   1006   1007    224    245    533   1942   
5        6   1199    565    993    567   1118   1806   1151   1146   1032   
6        7    178    722    243    693    935    129   1290   1498   1501   
7        8    228   1943   2164    492   1197     88   2325    232    884   
8        9   1918   1506   1743   2665   1798   1061   2738    911     70   
9       10    134   2604    410   2275   2285    305    409    306    221   
10      11    219   1609   2324    369   2300   1153   2026    462   2281   
11      12    512   1765    683   2547   1683    568   2063   2559    235   
12      13    585   1999    138   1794    818   1819   1439   1416    662   
13      14    942    908    931   1257    934    504   2488   1440    805   
14      15     90     38   1745    677     27   1072   1463   1461   1462   
15      16     39   2195    637   1778    251   1439   1670   1724   1851   
16      17    212   1313     31   1012     67   1163   2003   1887     32   
17      18    814   2210   1865   1025   1438    231    414   1247   1007   
18      19     31    715    348   1675   2118    417   1566   2017   2739   
19      20   2328     47    774   1548    584   1547   1546    148    779   
20      21    739   1053    591     94    348    733    244   1570   1430   
21      22    566   2038   2395   2494   2450    222   1896     10     28   
22      23     29    617   2102   2061    652   2343   1999    714   2121   
23      24   2383    148    589   1607   1603   2357   2360   1601   1604   
24      25   1643    923    238    172    259    129   1373    211    962   
25      26    236    252   1660   2457   1980    275    832    138   1794   
26      27   1745     90     38     15   1883    277    652    189   1167   
27      28   1351    567   2494   1896    228     22    111     63    422   
28      29     23   1208    498    617   2624    485   2146    360      8   
29      30    870   1013    822     63    360    334   2190     13   2242   
...    ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
2717  2718   1250   2717   2720   2492   2637    697    705    706   2633   
2718  2719   2078   2099    780    583   2376    585   1842   2731    702   
2719  2720   1249   1250   2718   2717   2678   1181   1315   2637   1649   
2720  2721   2271   1048   1264   1823   2147   2289   2075    335   1217   
2721  2722    985   2438   2339   1013   2622   2170    885    888   1549   
2722  2723   1999   1391   2542   2521   2667   1365   2658   1660    163   
2723  2724   2451   2512   2669   2284   2544   2690   2533   2554   2733   
2724  2725   1926   2145   1060   2498   2519    925   1320   1951    309   
2725  2726   1864    927    595   1294   1983    596     75     76   1985   
2726  2727   2364   2728    408   2385   2071   2391   1188   1187   1183   
2727  2728   2364   2727   2391   2071   1188   1187   1183   1185   1184   
2728  2729   1660   1534    770    274   1087    126    728    998     64   
2729  2730   2716   2241   2536   2520   2463    671    258   2561   2594   
2730  2731   2078   2099    583    780   2719   2463   2376    585   2572   
2731  2732   2653   2574   2442   2438   1896   2343   1403    259   2260   
2732  2733   2451   2512   2544   2669   2284   2724   2690   2197   2533   
2733  2734   1829   1227    656   1340    655    466   1345    179    654   
2734  2735   2451   2512   2669   2605   2284   2690   2724   2544   2124   
2735  2736    467   2555     69    214    691    888   1551   2120   2640   
2736  2737   1712   1851   2488     14   2706   1341   2313   1735   1818   
2737

In [89]:
df_result['id'][105]

106

In [91]:
df_result.to_csv('Recommender.csv', encoding='utf-8', index=None)